In [ ]:
import asyncio
from random import randint
from typing import Annotated

from agent_framework import Agent, tool
from agent_framework.observability import configure_otel_providers, get_tracer
from opentelemetry.trace import SpanKind
from opentelemetry.trace.span import format_trace_id
from pydantic import Field
from agent_framework.azure import AzureOpenAIResponsesClient
from azure.identity.aio import AzureCliCredential

import os
from dotenv import load_dotenv

In [2]:
load_dotenv(override=True)

project_endpoint = os.getenv("AZURE_AI_PROJECT_ENDPOINT")
model = os.getenv("AZURE_OPENAI_RESPONSES_DEPLOYMENT_NAME")

print("Project Endpoint: ", project_endpoint)
print("Model: ", model)

Project Endpoint:  https://jdramkumar32-1674-resource.services.ai.azure.com/api/projects/jdramkumar32-1674
Model:  gpt-4o


In [3]:
@tool(approval_mode="never_require")
async def get_weather(
    location: Annotated[str, Field(description="The location to get the weather for.")],
) -> str:
    """Get the weather for a given location."""
    await asyncio.sleep(randint(0, 10) / 10.0)  # Simulate a network call
    conditions = ["sunny", "cloudy", "rainy", "stormy"]
    return f"The weather in {location} is {conditions[randint(0, 3)]} with a high of {randint(10, 30)}°C."

In [5]:
configure_otel_providers()

In [ ]:
questions = ["What's the weather in Amsterdam?",
             "and in Paris, and which is better?", "Why is the sky blue?"]

with get_tracer().start_as_current_span("Scenario: Agent Chat", kind=SpanKind.CLIENT) as current_span:
    print(
        f"Trace ID: {format_trace_id(current_span.get_span_context().trace_id)}")

    credential = AzureCliCredential()
    client = AzureOpenAIResponsesClient(
        project_endpoint=project_endpoint,
        deployment_name=model,
        credential=credential,
    )

    agent = client.as_agent(
        name="CustomBot",
        instructions="You are a helpful assistant that remembers our conversation.",
        tools=[get_weather],
        id="custom-bot-001",
    )

    thread = agent.create_session()

    for question in questions:
        print(f"\nUser: {question}")
        print(f"{agent.name}: ", end="")
        async for update in agent.run(
            question,
            session=thread,
            stream=True,
        ):
            if update.text:
                print(update.text, end="")

Trace ID: 17e8ab0750097e3821db72f0f4b37ff6

User: What's the weather in Amsterdam?
CustomBot: The weather in Amsterdam is sunny with a high of 25°C. Enjoy your day!
User: and in Paris, and which is better?
CustomBot: {
    "resource_metrics": [
        {
            "resource": {
                "attributes": {
                    "telemetry.sdk.language": "python",
                    "telemetry.sdk.name": "opentelemetry",
                    "telemetry.sdk.version": "1.39.1",
                    "service.name": "agent_framework",
                    "service.version": "1.0.0b260212"
                },
                "schema_url": ""
            },
            "scope_metrics": [
                {
                    "scope": {
                        "name": "agent_framework",
                        "version": "1.0.0b260212",
                        "schema_url": "",
                        "attributes": null
                    },
                    "metrics": [
                  

{
    "name": "chat gpt-4o",
    "context": {
        "trace_id": "0x17e8ab0750097e3821db72f0f4b37ff6",
        "span_id": "0x5569524c8d738760",
        "trace_state": "[]"
    },
    "kind": "SpanKind.INTERNAL",
    "parent_id": "0x4242914d3548a31e",
    "start_time": "2026-02-20T10:48:21.803074Z",
    "end_time": "2026-02-20T10:48:24.059513Z",
    "status": {
        "status_code": "UNSET"
    },
    "attributes": {
        "gen_ai.input.messages": "[{\"role\": \"system\", \"parts\": [{\"type\": \"text\", \"content\": \"You are a helpful assistant that remembers our conversation.\"}]}, {\"role\": \"user\", \"parts\": [{\"type\": \"text\", \"content\": \"Why is the sky blue?\"}]}]",
        "gen_ai.system_instructions": "[{\"type\": \"text\", \"content\": \"You are a helpful assistant that remembers our conversation.\"}]",
        "gen_ai.request.choice.count": 1,
        "gen_ai.operation.name": "chat",
        "gen_ai.provider.name": "azure.ai.openai",
        "server.address": "Unk